# Analyze dataframes

for all csv-files:
    load dataframe
    find period where only one contender is active

In [22]:
import matplotlib.pyplot as plt
import numpy as np

In [1]:
# start by defining a Project name
project = 'medicin_prices'
import os # generel package for interacting with the system
# among other things automate folder creation

subfolders = ['raw_data','parsed_data']

raw_data = os.path.join(project, subfolders[0])
# Special folder that is write protected in order to preserve the original data
raw_data_read_only = os.path.join(project, subfolders[0] + '-read-only')
raw_data_read_only_limited = os.path.join(project, subfolders[0] + '-read-only-lmt')
parsed_data = os.path.join(project, subfolders[1])
work_on_dir = raw_data_read_only

In [2]:
# Get all csv files
import glob

def get_csv_files(data_path):
    return glob.glob(os.path.join(data_path, '*.csv'))

In [3]:
from pandas import DataFrame

def find_single_contender_idx(df: DataFrame):
    return df.isnull().sum(axis=1) == df.shape[1] - 1

In [4]:
def clean_dataframe(df: DataFrame):
    # Remove these columns if they are present in the data frame
    unwanted_columns = ['Unnamed: 0', 'tilskudspris']
    for unwanted_column in unwanted_columns:
        if unwanted_column in df.columns:
            df.drop(unwanted_column, axis=1, inplace=True)
    # Convert datetime column into a datetime time and store it in date
    df['date'] = pd.to_datetime(df['datetime'], format='%d.%m.%Y')
    # Drop the datetime column
    df.drop('datetime', axis=1, inplace=True)
    # Set the date column to be the index
    df.set_index('date', inplace=True)
    # Find index set with only one contender
    tmp = df[find_single_contender_idx(df)]
    # There might have been multiple contender from product launch
    if not tmp.empty:
        # Grab the first index of these
        new_start_index = tmp.index.values[0]
        # Slice such that we skip only NaN rows from the start
        df = df[new_start_index:].copy()
    return df

In [5]:
def find_pct_above_idx(df: DataFrame, threshold=0.5):
    return ((df > threshold).sum(axis=1) > 0 & (find_single_contender_idx(df)))

In [6]:
def find_pct_change_above(df: DataFrame, threshold=0.5):
    return df.loc[((df > threshold).sum(axis=1) > 0) & (df.isnull().sum(axis=1) == df.shape[1] - 1), :]

In [7]:
csv_files_limited = get_csv_files(raw_data_read_only)

In [8]:
csv_files_limited[:10]

['medicin_prices/raw_data-read-only/076043.csv',
 'medicin_prices/raw_data-read-only/070380.csv',
 'medicin_prices/raw_data-read-only/527140.csv',
 'medicin_prices/raw_data-read-only/373077.csv',
 'medicin_prices/raw_data-read-only/147370.csv',
 'medicin_prices/raw_data-read-only/075494.csv',
 'medicin_prices/raw_data-read-only/536076.csv',
 'medicin_prices/raw_data-read-only/518668.csv',
 'medicin_prices/raw_data-read-only/088392.csv',
 'medicin_prices/raw_data-read-only/057927.csv']

In [9]:
from typing import List
import pandas as pd
import re

# A product number regex matcher
product_number_matcher = re.compile('[0-9]{6}')

def find_all_above_idx(csv_files: List[str], pct_threshold=0.5, periods=2):
    """Run through a list of csv files and find entries above a percentage threshold given a number of periods

    Keyword arguments:
        csv_files     -- A list of paths point to csv files
        pct_threshold -- Percentage threshold that the price hike should be larger than (defaults to 50%, i.e. 0.5)
        periods       -- Periods defines the periods between measurements to compute the percentage difference between.
                         e.g. periods=2, compute between, period 1: x_2 / x_1, period 2: x_3 / x_1
    """
    # Create a dictionary for storing the results
    product_numbers = dict()
    # Keep track of product numbers already processed
    already_processed = []
    # Run throught all the csv files we where given
    for f in csv_files:
        # Find product number
        product_number = product_number_matcher.search(f).group()
        # Check whether the product number has already been processed
        if product_number in already_processed:
            continue
        # Read the csv file
        df = pd.read_csv(f)
        # Clean the data frame
        df = clean_dataframe(df)
        # Check if we have already processed the product number before
        already_processed.extend(df.columns.tolist())
        # Find percentage change over the number of periods
        pct_changed = df.pct_change(periods)
        # Find places where there are only one contender
        single_pct_idx = find_single_contender_idx(pct_changed)
        # Find all periods where the percentage change is above the given threshold
        above_pct = find_pct_above_idx(pct_changed[single_pct_idx], threshold=pct_threshold)
        idxs = find_pct_above_idx(pct_changed[single_pct_idx], threshold=pct_threshold)
        
        # Store the result, if the frame has any True in the index set
        if above_pct.any():
            product_numbers[product_number] = above_pct
    # Return result
    return product_numbers

In [10]:
def find_all_above(csv_files: List[str], pct_threshold=0.5, periods=2):
    """Run through a list of csv files and find entries above a percentage threshold given a number of periods

    Keyword arguments:
        csv_files     -- A list of paths point to csv files
        pct_threshold -- Percentage threshold that the price hike should be larger than (defaults to 50%, i.e. 0.5)
        periods -- Periods defines the periods between measurements to compute the percentage difference between.
                   e.g. periods=2, compute between, period 1: x_2 / x_1, period 2: x_3 / x_1
    """
    # Create a dictionary for storing the results
    product_numbers = dict()
    # Keep track of product numbers already processed
    already_processed = []
    # Run throught all the csv files we where given
    for f in csv_files:
        # Find product number
        product_number = product_number_matcher.search(f).group()
        # Check whether the product number has already been processed
        if product_number in already_processed:
            continue
        # Read the csv file
        df = pd.read_csv(f)
        # Clean the data frame
        df = clean_dataframe(df)
        # Check if we have already processed the product number before
        already_processed.extend(df.columns.tolist())
        # Find percentage change over the number of periods
        pct_changed = df.pct_change(periods)
        # Find places where there are only one contender
        single_pct_frame = pct_changed[find_single_contender_idx(pct_changed)]
        # Find all periods where the percentage change is above the given threshold
        above_pct = find_pct_change_above(single_pct_frame, threshold=pct_threshold)
        above_idx = find_pct_above_idx(single_pct_frame, threshold=pct_threshold)
        # Store the result, if the frame is non empty
        if not above_pct.empty:
            product_numbers[product_number] = {'pct_change': above_pct, 'idx': above_idx}
    # Return result
    return product_numbers

In [16]:
tmp = find_all_above(csv_files_limited, pct_threshold=7.5, periods=10)

In [19]:
def pretty_print_frames(d):
    for pn, frame in d.items():
        if not frame['pct_change'].empty:
            print('Product number: ', pn)
            print(frame['pct_change'].head())
            print(frame['idx'][frame['idx'] == True].head())
        # Only print the first element
        break

In [20]:
pretty_print_frames(tmp)

Product number:  412129
            412129  145077  507563
date                              
2013-01-07     NaN    99.0     NaN
2013-01-21     NaN    99.0     NaN
2013-02-04     NaN    99.0     NaN
2013-02-18     NaN    99.0     NaN
2013-03-04     NaN    99.0     NaN
date
2013-01-07    True
2013-01-21    True
2013-02-04    True
2013-02-18    True
2013-03-04    True
dtype: bool


In [36]:
work_on = {'062826': tmp['062826']}

In [37]:
work_on['062826']['idx'].head()

date
2010-11-01    False
2010-11-15    False
2010-11-29    False
2010-12-13    False
2010-12-27    False
dtype: bool

In [38]:
work_on['062826']['idx'].index

DatetimeIndex(['2010-11-01', '2010-11-15', '2010-11-29', '2010-12-13',
               '2010-12-27', '2011-01-10', '2011-01-24', '2011-02-07',
               '2011-02-21', '2011-03-07',
               ...
               '2015-04-27', '2015-05-11', '2015-05-25', '2015-06-08',
               '2015-06-22', '2015-07-06', '2015-07-20', '2015-08-03',
               '2015-08-17', '2015-08-31'],
              dtype='datetime64[ns]', name='date', length=122, freq=None)

In [39]:
from datetime import datetime
from datetime import timedelta

def add_periods(date: datetime, periods: int) -> datetime:
    """Function for adding a number of periods to a datetime

    Keyword arguments:
        date    -- A datetime to add a number of 14 days periods to
        periods -- Number of periods to add to the datetime
    Returns:
        The date plus a number of periods (periods can be negative)
    """
    number_of_days_to_add = periods * 14
    return date + timedelta(days=number_of_days_to_add)

def extraction_period(date: datetime, periods: int=8) -> (datetime, datetime):
    """Function for creating a date +/- a number of periods

    Keyword arguments:
        date    -- A datetime to add a number of 14 days periods to
        periods -- Number of periods to add to the datetime
    Returns:
        A tuple of two dates, such that tuple = (datetime1, datetime2), where datetime1 = date - period,
        datetime2 = date + period
    """    
    return (add_periods(date, -periods), add_periods(date, periods))

In [40]:
def extract_above_indices(d_elem):
    """Function for extracting indices from a bool sets where it is True

    Keyword arguments:
        d_elem   -- A dictionary element containing a ['idx'] value containing a dataframe or series with bools
    Returns:
        Index set
    """
    return d_elem['idx'][d_elem['idx'] == True].index

In [42]:
date_index_set = extract_above_indices(work_on['062826'])
print(date_index_set)

DatetimeIndex(['2013-06-10', '2013-06-24', '2013-07-08', '2014-09-29',
               '2014-10-13', '2014-10-27', '2014-11-10', '2014-11-24'],
              dtype='datetime64[ns]', name='date', freq=None)


In [43]:
def expand_date_indices(date_indices, periods=8):
    """Function for expanding a list of dates into a list of tuples of dates

    Keyword arguments:
        date_indices -- A datetime index
        periods      -- Number of periods to expand each date with
    Returns:
        A list of tuples l = [t_1, t_2, ..., t_n], such that t_i = (date_i - periods, date_i + periods)
    """
    expanded_date_list = []
    for date_elem in date_indices:
        expanded_date = extraction_period(date_elem, periods=periods)
        expanded_date_list.append(expanded_date)
    return expanded_date_list

In [44]:
test_date_expansion = expand_date_indices(date_index_set)
print(test_date_expansion)

[(Timestamp('2013-02-18 00:00:00'), Timestamp('2013-09-30 00:00:00')), (Timestamp('2013-03-04 00:00:00'), Timestamp('2013-10-14 00:00:00')), (Timestamp('2013-03-18 00:00:00'), Timestamp('2013-10-28 00:00:00')), (Timestamp('2014-06-09 00:00:00'), Timestamp('2015-01-19 00:00:00')), (Timestamp('2014-06-23 00:00:00'), Timestamp('2015-02-02 00:00:00')), (Timestamp('2014-07-07 00:00:00'), Timestamp('2015-02-16 00:00:00')), (Timestamp('2014-07-21 00:00:00'), Timestamp('2015-03-02 00:00:00')), (Timestamp('2014-08-04 00:00:00'), Timestamp('2015-03-16 00:00:00'))]


In [45]:
from typing import Tuple
from copy import deepcopy

def merge_periods(dates: List[Tuple[datetime, datetime]]) -> List[Tuple[datetime, datetime]]:
    """Function for merging time periods if they overlap, takes a list of tuples containing datetime elements.

    Keyword arguments:
        dates -- A list of tuples containing datetime elements. The function takes two consecutive tuples t1 and t2
                 and merges them into a single tuple if they overlap
    Returns:
        A list of tuples of non overlap date periods
    """
    def date_intersection(dt1: datetime, dt2: datetime) -> bool:
        """Helper function that determines if the second element of dt1 is containg within dt2
        
        Returns:
            True if there is overlap, False otherwise
        """
        return dt1[1] >= dt2[0] and dt1[1] < dt2[1]
    
    def merge_tuple(t1: Tuple[datetime, datetime], t2: Tuple[datetime, datetime]) -> Tuple[datetime, datetime]:
        """Helper function that merges two tuple into a single tuple

        Returns:
            A new tuple such that t_new = (dt1[0], dt2[1])
        """        
        return (t1[0], t2[1])
    
    def has_intersections(date_list):
        """Helper function that determines whether a list of date tuples still have intersections (overlap

        Returns:
            True if intersections exists, False otherwise
        """                
        intersects = []
        for i in range(len(date_list)-1):
            d1 = date_list[i]
            d2 = date_list[i+1]
            dates_intersects = date_intersection(d1, d2)
            intersects.append(dates_intersects)
        any_intersections = any(intersects)
        return any(intersects)

    # Make a copy of our dates, otherwise we change the original list
    compute_list = deepcopy(dates)
    # Sanity check, does our list of dates contain more than one tuple
    if len(compute_list) == 1:
        return compute_list
    # Loop while the sorted list of date tuples still has intersections
    while has_intersections(sorted(compute_list)):
        # Extract two dates tuples, date1 = (datetime1, datetime2)
        date1 = compute_list.pop(0)
        date2 = compute_list.pop(0)
        # does the dates tuples intersect / is there overlap in the time period?
        if date_intersection(date1, date2):
            # The two dates overlapped, merge them into a new date tuple
            new_date = merge_tuple(date1, date2)
            # Append the new date tuple to the list
            compute_list = [new_date] + compute_list
        else:
            # No overlap was found, simply append the dates to the end of the list (we pop from the start of the list)
            compute_list.append(date1)
            compute_list.append(date2)
        # We have merged everything except for one element, hence we need to break the while loop
        if len(compute_list) == 1:
            break
    # Return the merged result sorted
    return sorted(compute_list)

In [46]:
test_merge_dates = merge_periods(test_date_expansion)
test_merge_dates

[(Timestamp('2013-02-18 00:00:00'), Timestamp('2013-10-28 00:00:00')),
 (Timestamp('2014-06-09 00:00:00'), Timestamp('2015-03-16 00:00:00'))]

In [51]:
def load_product_dataframe(product_number) -> DataFrame:
    """Function for loading a dataframe given a product number

    Keyword arguments:
        product_number -- product number for which to load a dataframe

    Returns:
        A cleaned dataframe
    """
    df_path = os.path.join(work_on_dir, '{}.csv'.format(product_number))
    df = clean_dataframe(pd.read_csv(df_path))
    return df

In [52]:
# start by defining a Project name
project = 'medicin_prices'
import os # generel package for interacting with the system
# among other things automate folder creation
def maybe_create_dir(path):
    if not os.path.isdir(path):
        os.mkdir(path)

maybe_create_dir(project)

subfolders = ['images']

for directory in subfolders: 
    maybe_create_dir(os.path.join(project, directory))

In [19]:
import matplotlib.pyplot as plt
import seaborn as sns

def generate_plot_and_save(df: DataFrame, start_date: datetime, end_date: datetime, save_path):
    # Set figure size
    fig = plt.figure(figsize=(15,15))
    # extract the period of time we want to plot, make a copy
    plot_data = df.loc[start_date:end_date].copy()
    # if we have more than one column, drop any column that are all NaN
    if len(plot_data.columns.tolist()) > 1:
        plot_data.dropna(axis=1, inplace=True, how='all')
    # Extract the name of the column that are 'single' at the point of price hike
    product_name = plot_data.columns[plot_data.notnull().any() == True][0]
    # Set title
    plt.title('Prisstigning for produkt nummer: {}'.format(product_name)) # , fontdict = {'fontsize' : 20}
    # Increase font size to make it look nice
    plt.rc('axes', titlesize=28, labelsize=24)
    # If we only have one product in the plot, skip having a legend
    legend_type = False if len(plot_data.columns.tolist()) == 1 else 'full'
    # Make a line plot of the data
    g = sns.lineplot(data=plot_data, legend=legend_type)
    # If there is a legend, increase font size
    if legend_type:
        plt.setp(g.get_legend().get_texts(), fontsize='18') # for legend text
        plt.setp(g.get_legend().get_title(), fontsize='20') # for legend title
    # Increase linewidth
    for l in g.lines:
        plt.setp(l,linewidth=3)
    # Set x- and y-labels
    plt.xlabel('Dato (åååå-mm)')
    plt.ylabel('Pris (kr)')
    # Increase font on x- and y-ticks, also rotate xticks 45 degrees
    plt.xticks(fontsize=20, rotation=45)
    plt.yticks(fontsize=20)
    # Get dates for plot name
    start_tag = start_date.date()
    end_tag = end_date.date()
    # Save the figure
    plt.savefig('{}_{}_{}.png'.format(os.path.join(save_path, product_name), start_tag, end_tag))
    # Close the figure after saving to disk to preserve memory
    plt.close(fig)

NameError: name 'datetime' is not defined

In [54]:
def generate_all_plots(dictionary, save_dir=os.path.join(project, 'images')):
    for pn, pct_idx in dictionary.items():
        print('Generating plot for: {}'.format(pn))
        idxs = extract_above_indices(pct_idx)
        expanded_dates = expand_date_indices(idxs, periods=16)
        merged_dates = merge_periods(expanded_dates)
        product_dataframe = load_product_dataframe(pn)
        for period in merged_dates:
            start_date, end_date = period
            generate_plot_and_save(product_dataframe, start_date, end_date, save_dir)

In [55]:
# Required by pandas for future versions
from pandas.plotting import register_matplotlib_converters
register_matplotlib_converters()

generate_all_plots(tmp)

Generating plot for: 412129
Generating plot for: 062826
Generating plot for: 512521
Generating plot for: 570006
Generating plot for: 077640
Generating plot for: 012718
Generating plot for: 447449
Generating plot for: 032660
Generating plot for: 599280
Generating plot for: 145958
Generating plot for: 092171
Generating plot for: 414991
Generating plot for: 010234
Generating plot for: 104992
Generating plot for: 110333
Generating plot for: 407740
Generating plot for: 126093
Generating plot for: 397192
Generating plot for: 056732
Generating plot for: 133440
Generating plot for: 191986
Generating plot for: 066354
Generating plot for: 074733
Generating plot for: 466696
Generating plot for: 483749
Generating plot for: 012693
Generating plot for: 170298


In [11]:
def find_atleast_contender_idx(df: DataFrame, contenders=1):
    return df.isnull().sum(axis=1) <= df.shape[1] - contenders

In [12]:
from tqdm import tqdm_notebook as tqdm

def find_streaks(csv_files: List[str]):
    """Run through a list of csv files and find entries above a percentage threshold given a number of periods

    Keyword arguments:
        csv_files  -- A list of paths point to csv files
    """
    # Create a dictionary for storing the results
    product_numbers = dict()
    # Keep track of product numbers already processed
    already_processed = []
    # Run throught all the csv files we where given
    for i in tqdm(range(len(csv_files))):
        f = csv_files[i]
        # Find product number
        product_number = product_number_matcher.search(f).group()
        # Check whether the product number has already been processed
        if product_number in already_processed:
            continue
        # Read the csv file
        df = pd.read_csv(f)
        # Clean the data frame
        df = clean_dataframe(df)
        df_columns = df.columns.tolist()
        # Check if we have already processed the product number before
        already_processed.extend(df_columns)
        # We are only interested in dataframe that has atleast two columns
        if len(df_columns) < 2:
            continue
        # Extract indices where there are atleast two contenders
        df['min_idx'] = df.idxmin(axis=1)
         # At least two contenders, plus one for the min_idx column
        two_or_more_idx = find_atleast_contender_idx(df.drop(['min_idx'], axis=1), 2)
        df_two_or_more = df.loc[two_or_more_idx].copy()
        df_two_or_more['category-code'] = pd.Categorical(df_two_or_more['min_idx']).codes
        product_numbers[product_number] = df_two_or_more
        
    # Return result
    return product_numbers

In [13]:
test = find_streaks(csv_files_limited)

In [26]:
from mpl_toolkits.axes_grid1 import make_axes_locatable
import matplotlib as mpl
from matplotlib import cm

def save_min_product_price_plot(product_number, df, save_path=os.path.join(project, 'images')):
    
    # Find number of different categories
    unique_cats = df['category-code'].unique()
    # Find number of 'bins'
    num_bins = df['category-code'].shape[0]
    # Find category minimum value
    min_value = unique_cats.min()
    # Find category maximum value
    max_value = unique_cats.max()
    # Define the colormap
    cmap = plt.cm.jet
    # Define the bins and normalize
    bounds = np.linspace(min_value, max_value, len(unique_cats))
    norm = mpl.colors.BoundaryNorm(bounds, cmap.N)
    df_plot = pd.DataFrame((np.array(df['category-code'])))
    fig = plt.figure(figsize=(14,1))
    ax = plt.subplot()
    # Transpose the category data to make a horizontal plot
    im = ax.imshow(df_plot.transpose(),
                   cmap=cmap,
                   interpolation=None,
                   vmin=min_value,
                   vmax=max_value,
                   aspect='auto',
                   norm=norm)
    # Remove ticks from top, bottom and left axis, and distable labels
    plt.tick_params(
        axis='both',       # changes apply to the x-axis
        which='both',      # both major and minor ticks are affected
        bottom=False,      # ticks along the bottom edge are off
        top=False,         # ticks along the top edge are off
        left=False,        # ticks along the left edge are off
        labelbottom=False) # labels along the bottom edge are off
    # Make axis locatable 
    divider = make_axes_locatable(ax)
    # Append an axis to the right
    cbax = divider.append_axes("right", size="5%", pad=0.10)
    # Add a colorbar to the right axis
    cb = plt.colorbar(im,
                      cax=cbax,
                      cmap=cmap,
                      boundaries=bounds,
                      spacing='proportional')
    # Set the colorbar label
    cb.set_label('Category')
    # Disable formmatter on both axis
    ax.xaxis.set_major_formatter(plt.NullFormatter())
    ax.yaxis.set_major_formatter(plt.NullFormatter())
    # Save the figure as streak  plot
    plt.savefig('{}_streakplot.png'.format(os.path.join(save_path, product_number)))
    # Close the figure after saving to disk to preserve memory
    plt.close(fig)


In [32]:
def generate_all_streak_plots(dictionary, save_dir=os.path.join(project, 'images')):
    for pn, df in dictionary.items():
        if len(df['category-code'].unique()) == 1:
            continue
        print("processing: {}".format(pn))
        try:
            save_min_product_price_plot(pn, df)
        except ZeroDivisionError as zde:
            # We caught an error, remove the file
            if os.path.exists(os.path.join(project, 'images', '{}_steakplot.png'.format(pn))):
                os.remove(filePath)

In [34]:
generate_all_streak_plots(test)

processing: 076043
126
[4 1 2 3 0]
processing: 070380
241
[1 2 0]
processing: 527140
72
[3 0 2 1]
processing: 373077
151
[2 0 1]
processing: 147370
79
[2 0 3 4 1]
processing: 536076
7
[2 1 0]
processing: 518668
106
[0 3 2 4 1]
processing: 489609
183
[1 0]
processing: 458149
107
[1 0]
processing: 534135
115
[2 0 1]
processing: 565845
50
[1 0]
processing: 389809
93
[1 0]
processing: 020986
156
[3 0 2 1]
processing: 550317
153
[3 0 2 1]
processing: 452811
101
[0 2 3 1]
processing: 374968
219
[1 2 0 3]
processing: 589888
39
[0 1]
processing: 478728
40
[1 0 2]
processing: 012527
126
[0 1 2]
processing: 412129
167
[2 0 1]
processing: 518283
72
[1 2 0]
processing: 102769
306
[0 2 1]
processing: 504990
101
[2 0 1]
processing: 149891
206
[1 2 0 3]
processing: 463623
102
[1 0 3 2]
processing: 481849
206
[2 1 0 3]
processing: 453006
272
[0 1 2]
processing: 159858
26
[1 0]
processing: 079261
7
[0 1]
processing: 386953
7
[1 0]
processing: 130429
40
[0 1]
processing: 102895
105
[0 2 1]
processing: 1

/home/mian/bin/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:23: RuntimeWarning: More than 20 figures have been opened. Figures created through the pyplot interface (`matplotlib.pyplot.figure`) are retained until explicitly closed and may consume too much memory. (To control this warning, see the rcParam `figure.max_open_warning`).


processing: 564621
104
[2 0 1]
processing: 467071
153
[2 0 1]
processing: 583447
55
[2 3 1 4 0]
processing: 414188
271
[0 3 1 2]
processing: 055277
306
[1 0 2]
processing: 113412
166
[1 4 0 3 2]
processing: 161117
89
[0 1]
processing: 430868
175
[0 1]
processing: 107839
7
[3 1 2 0]
processing: 032173
108
[0 1 2]
processing: 095680
163
[0 1 2 3 4]
processing: 071860
453
[0 1 2]
processing: 033471
164
[0 3 1 2]
processing: 061212
7
[0 2 1]
processing: 140211
109
[2 0 1 3]
processing: 042347
139
[2 1 0 3]
processing: 416478
7
[0 1]
processing: 434534
156
[0 2 3 1 4]
processing: 005899
7
[0 1 2]
processing: 409793
55
[0 1]
processing: 513096
114
[1 2 0]
processing: 499797
235
[2 0 1 3]
processing: 027988
7
[0 2 1]
processing: 012487
7
[0 2 1]
processing: 474120
7
[3 2 1 0]
processing: 513417
96
[0 1 4 3 2]
processing: 045739
194
[2 1 0 3]
processing: 102796
300
[2 0 1]
processing: 129576
335
[1 0 3 4 2]
processing: 161720
7
[2 1 0]
processing: 490176
173
[4 1 2 0 3]
processing: 156596
156


processing: 056913
193
[0 2 1]
processing: 505394
48
[2 1 0]
processing: 547764
7
[2 1 0]
processing: 456833
86
[2 1 3 0]
processing: 515140
31
[0 1]
processing: 063365
44
[0 1]
processing: 458239
109
[2 1 0]
processing: 030936
219
[1 2 0 4 3]
processing: 006899
37
[1 0]
processing: 140591
81
[2 3 1 4 0]
processing: 189427
65
[2 0 1]
processing: 162149
149
[1 0]
processing: 105616
10
[0 1]
processing: 463424
91
[1 0]
processing: 551674
219
[0 1 3 2]
processing: 027231
212
[1 0 2 3 4]
processing: 067283
7
[0 1]
processing: 149772
323
[1 0 3 4 2]
processing: 170773
224
[0 2 1 4 3]
processing: 529403
120
[3 4 0 2 1]
processing: 597401
163
[1 0]
processing: 057554
238
[1 0 2]
processing: 382314
127
[0 1 3 2]
processing: 460293
12
[1 0]
processing: 116008
142
[2 0 1]
processing: 078591
190
[2 0 4 3 1]
processing: 463654
12
[0 1 2]
processing: 572901
48
[0 1]
processing: 077862
87
[1 2 0]
processing: 439035
116
[1 2 0]
processing: 518953
127
[3 4 2 0 1]
processing: 165863
160
[1 0 2]
process

processing: 031860
329
[1 0 2]
processing: 407515
209
[1 0 3 2 4]
processing: 383310
36
[1 0]
processing: 070046
206
[2 3 0 1]
processing: 028146
101
[0 2 1 3]
processing: 101961
43
[0 1]
processing: 025628
7
[0 1 2]
processing: 394720
98
[2 3 1 0]
processing: 027659
7
[1 0 2]
processing: 163445
151
[1 0 2]
processing: 062003
217
[1 0 2 3]
processing: 085473
51
[0 1]
processing: 576568
120
[2 1 0]
processing: 431098
178
[2 1 0]
processing: 513252
7
[0 1 2]
processing: 151687
144
[3 0 2 1]
processing: 031842
296
[0 1 2 3]
processing: 531364
194
[4 1 2 3 0]
processing: 399519
182
[0 1 2]
processing: 057833
103
[0 2 1]
processing: 553975
112
[1 0]
processing: 114013
165
[2 0 1]
processing: 079290
7
[2 0 1]
processing: 183101
209
[1 0 2 3 4]
processing: 559037
7
[2 1 0]
processing: 427644
124
[1 0]
processing: 534348
7
[1 0 2]
processing: 153671
137
[0 1 2 3]
processing: 551779
132
[3 0 2 1]
processing: 486653
119
[1 2 3 0]
processing: 192222
98
[2 3 1 0]
processing: 088384
353
[0 3 1 2 4]

...

<Figure size 1008x72 with 2 Axes>

ZeroDivisionError: division by zero

<Figure size 1008x72 with 2 Axes>

ZeroDivisionError: division by zero

<Figure size 1008x72 with 2 Axes>

In [99]:
test['439035'].to_csv(os.path.join('./', '439035_streak' + '.csv'))

In [87]:
test['439035']['category-code'].tail()

date
2019-06-17    1
2019-07-01    0
2019-07-15    1
2019-07-29    0
2019-08-12    1
Name: category-code, dtype: int8

In [94]:
dup_test = test['439035'].duplicated(subset=['category-code', 'min_idx'], )
dup_test.tail()

date
2019-06-17    True
2019-07-01    True
2019-07-15    True
2019-07-29    True
2019-08-12    True
dtype: bool

In [88]:
dup_test.tail()

date
2019-06-17    True
2019-07-01    True
2019-07-15    True
2019-07-29    True
2019-08-12    True
Name: category-code, dtype: bool

In [69]:
test_case = np.array([0,1]*5 + [1]*5 + [0]*4 + [1,0]*3)
test_case

array([0, 1, 0, 1, 0, 1, 0, 1, 0, 1, 1, 1, 1, 1, 1, 0, 0, 0, 0, 1, 0, 1,
       0, 1, 0])

In [74]:
cfilter = np.array([0, 1, 0])
test_convolve = np.convolve(test_case, cfilter, 'full')
test_convolve

array([0, 0, 1, 0, 1, 0, 1, 0, 1, 0, 1, 1, 1, 1, 1, 1, 0, 0, 0, 0, 1, 0,
       1, 0, 1, 0, 0])

In [83]:
# from itertools import izip

def grouped(iterable, n):
    "s -> (s0,s1,s2,...sn-1), (sn,sn+1,sn+2,...s2n-1), (s2n,s2n+1,s2n+2,...s3n-1), ..."
    return zip(*[iter(iterable)]*n)

# sliding
nfilter = [True, False]
test_signal = [False,True]*5 + [True]*5 + [False]*4 + [True,False]*3

some_list = []
for sub_list in grouped(test_signal, 2):
    print(sub_list)
    print(nfilter)
    some_list.append(nfilter == list(sub_list))
    
print(some_list)

(False, True)
[True, False]
(False, True)
[True, False]
(False, True)
[True, False]
(False, True)
[True, False]
(False, True)
[True, False]
(True, True)
[True, False]
(True, True)
[True, False]
(True, False)
[True, False]
(False, False)
[True, False]
(False, True)
[True, False]
(False, True)
[True, False]
(False, True)
[True, False]
[False, False, False, False, False, False, False, True, False, False, False, False]
